In [1]:
import pandas as pd
import en_core_web_lg
nlp =  en_core_web_lg.load()
import numpy as np
np.random.seed(0)
from pymongo import MongoClient
from spacy.matcher import Matcher
from spacy.tokenizer import Tokenizer

connection=MongoClient("mongodb://localhost:27017/crawler.contents")

db=connection.get_database()

[nltk_data] Downloading package wordnet to /home/visnja/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package stopwords to /home/visnja/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
/home/visnja/anaconda3/envs/python3.7-env/lib/python3.7/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:

articles = pd.DataFrame(list(db.contents.find()))
articles = articles.drop(columns=['visited','alternateImageUrl','created_at','contentType','date','icon','publishedAt','source','url'])



In [4]:


matcher = Matcher(nlp.vocab)
matcher.add('AUD', [
    [{'TEXT':{'REGEX':'[A-Z][A-Z][A-Z][/]?AUD'}}],
    [{'TEXT':{'REGEX':'AUD[/]?[A-Z][A-Z][A-Z]'}}],
    [{'LOWER':'aud'}],
    [{'LOWER':'aussie'}],
    [{"LOWER":'the','OP':'?'},{"LOWER":'australian'},{'LOWER':{'REGEX':'dollar[s]?'}}]
])
matcher.add('USD', [
    [{'TEXT':{'REGEX':'[A-Z][A-Z][A-Z][/]?USD'}}],
    [{'TEXT':{'REGEX':'USD[/?][A-Z][A-Z][A-Z]'}}],
    [{'LOWER':{'REGEX':'[-]?the'}},{"LOWER":'dollar'}],
    [{"LOWER":'us'},{'LOWER':{'REGEX':'dollar[s]?'}}],
    [{"LOWER":'u.s.'},{'LOWER':{'REGEX':'dollar[s]?'}}],
    [{"POS":'ADJ'},{'LOWER':{'REGEX':'dollar[s]?'}}],
    [{"DEP": "compound","OP": "?"},{'LOWER':{'REGEX':'dollar[s]?'}}],
    [{"LOWER":"usd"}]
])
matcher.add('EUR', [
    [{'TEXT':{'REGEX':'[A-Z][A-Z][A-Z][/]?EUR'}}],
    [{'TEXT':{'REGEX':'EUR[/]?[A-Z][A-Z][A-Z]'}}],
    [{'LOWER':'eur'}],
    [{'LOWER':'the','OP':'?'},{'LOWER':{'REGEX':'euro[s]?[.]?'}}]
])
matcher.add('GBP', [
    [{'TEXT':{'REGEX':'[A-Z][A-Z][A-Z][/]?GBP'}}],
    [{'TEXT':{'REGEX':'GBP[/]?[A-Z][A-Z][A-Z]'}}],
    [{'LOWER':'gbp'}],
    [{'LOWER':'the','OP':'?'},{'LOWER':'british','OP':'?'},{'LOWER':{'REGEX':'pound[s]?'}}],
    [{'LOWER':{'REGEX':'[-]?sterling[s]?'}}]
])
matcher.add('CHF', [
    [{'TEXT':{'REGEX':'[A-Z][A-Z][A-Z][/]?CHF'}}],
    [{'TEXT':{'REGEX':'CHF[/]?[A-Z][A-Z][A-Z]'}}],
    [{'LOWER':'chf'}],
    [{'LOWER':'swissie'}],
    [{'LOWER':'swiss'},{'LOWER':{'REGEX':'franc[s]?'}}]])
matcher.add('CAD', [
    [{'LOWER':'cad'}],
    [{'LOWER':'cdn'}],
    [{'TEXT':{'REGEX':'[A-Z][A-Z][A-Z][/]?CAD'}}],
    [{'TEXT':{'REGEX':'CAD[/]?[A-Z][A-Z][A-Z]'}}],
    [{'LOWER':'canadian'},{'LOWER':{'REGEX':'dollar[s]?'}}]])
matcher.add('CNY', [
    [{'LOWER':'cny'}],
    [{'TEXT':{'REGEX':'[A-Z][A-Z][A-Z][/]?CNY'}}],
    [{'TEXT':{'REGEX':'CNY[/]?[A-Z][A-Z][A-Z]'}}],
    [{'LOWER':'the','OP':'?'},{'LOWER':'chinese'},{'LOWER':'yuan'},{"IS_PUNCT": True,'OP':'?'}],
    [{'LOWER':{'REGEX':'yuan[s]?'}}]
                   ])
matcher.add('TWD', [
    [{'TEXT':{'REGEX':'[A-Z][A-Z][A-Z][/]?TWD'}}],
    [{'TEXT':{'REGEX':'TWD[/]?[A-Z][A-Z][A-Z]'}}],
    [{'LOWER':'twd'}],
    [{'LOWER':'taiwan'},{'LOWER':'new','OP':'?'},{'LOWER':{'REGEX':'dollar[s]?'}}]
    ])
matcher.add('NZD', [
    [{'TEXT':{'REGEX':'[A-Z][A-Z][A-Z][/]?NZD'}}],
    [{'TEXT':{'REGEX':'NZD[/]?[A-Z][A-Z][A-Z]'}}],
    [{'LOWER':'nzd'}],
    [{'LOWER':'kiwi'}],
    [{'LOWER':'new'},{'LOWER':'zealand'},{'LOWER':{'REGEX':'dollar[s]?'}}]
])
matcher.add('BTC', [
    [{'TEXT':{'REGEX':'[A-Z][A-Z][A-Z][/]?BTC'}}],
    [{'TEXT':{'REGEX':'BTC[/]?[A-Z][A-Z][A-Z]'}}],
    [{'LOWER':'btc'}],
    [{'LOWER':{'REGEX':'bitcoin[s]?'}}]
])
matcher.add('JPY', [
    [{'TEXT':{'REGEX':'[A-Z][A-Z][A-Z][/]?JPY'}}],
    [{'TEXT':{'REGEX':'JPY[/]?[A-Z][A-Z][A-Z]'}}],
    [{'LOWER':'jpy'}],
    [{'LOWER':'japanese'},{'LOWER':{'REGEX':'yen[s]?'}}],
    [{'LOWER':'the','OP':'?'},{'LOWER':{'REGEX':'yen[s]?'}}]
])
matcher.add('TRY', [
    [{'LOWER':'try'}],
    [{'TEXT':{'REGEX':'[A-Z][A-Z][A-Z][/]?TRY'}}],
    [{'TEXT':{'REGEX':'TRY[/]?[A-Z][A-Z][A-Z]'}}],
    [{'LOWER':'turkish'},{'LOWER':{'REGEX':'lira[s]?'}}],
    [{'LOWER':{'REGEX':"turkey's?"}},{'LOWER':{'REGEX':'lira[s]?'}}],
    
])
matcher.add('ARS', [
    [{'LOWER':'ars'}],
    [{'TEXT':{'REGEX':'[A-Z][A-Z][A-Z][/]?ARS'}}],
    [{'TEXT':{'REGEX':'ARS[/]?[A-Z][A-Z][A-Z]'}}],
    [{'LOWER':'argentine'},{'LOWER':{'REGEX':'peso[s]?'}}],
    
])
matcher.add('MXN', [
    [{'TEXT':{'REGEX':'[a-z][a-z][a-z]MXN'}}],
    [{'TEXT':{'REGEX':'MXN[/]?[A-Z][A-Z][A-Z]'}}],
    [{'LOWER':'mxn'}],
    [{'LOWER':'mexican'},{'LOWER':{'REGEX':'peso[s]?'}}],
    [{'LOWER':'mexican'},{'LOWER':{'REGEX':'currenc[y|ies]?'}}]
    
])

matcher.add('RUB', [
    [{'LOWER':'rub'}],
    [{'TEXT':{'REGEX':'[A-Z][A-Z][A-Z][/]?RUB'}}],
    [{'TEXT':{'REGEX':'RUB[/]?[A-Z][A-Z][A-Z]'}}],
    [{'LOWER':'russian'},{'LOWER':{'REGEX':'ruble[s]?'}}],
    [{'LOWER':{'REGEX':'ruble[s]?'}}]
    
])
matcher.add('OIL', [
    [{'LOWER':'crude'},{'LOWER':{'REGEX':'oil[s]?'}}],
])
matcher.add('XAU', [
    [{'TEXT':{'REGEX':'[A-Z][A-Z][A-Z][/]?XAU'}}],
    [{'TEXT':{'REGEX':'XAU[/]?[A-Z][A-Z][A-Z]'}}],
    [{'LOWER':'xau'}],
    [{'LOWER':'gold'},{'LOWER':{'REGEX':'price[s]?'}}],
])
matcher.add('INDEX',[
    [{'LOWER':'nasdaq100'}],
    [{'LOWER':'nasdaq'},{'ORTH':"100"}],
    [{'LOWER':'s&p500'}],
    [{'LOWER':'sp500'}],
    [{"LOWER": "sp"}, {"ORTH": "500"}],
    [{"LOWER": "s&p"}],
    [{"LOWER": "s&p"}, {"ORTH": "500"}],
    [{'LOWER':'dow'},{'LOWER':'jones'}],
    [{'LOWER':'djia'}],
    [{'LOWER':'dow'},{'LOWER':'jones'},{'LOWER':'industrial'},{'LOWER':'average'}],
    [{'LOWER':'ftse'},{"ORTH": '100','OP':'?'}],
    [{'LOWER':'financial'},{'LOWER':'times'},{'LOWER':'stock'},{'LOWER':'exchange'}],
    [{'LOWER':'footsie'}],
    [{'LOWER':'dax'}],
    [{'LOWER':'dax'},{"ORTH": '40','OP':'?'}],
    [{'LOWER':'german'},{'LOWER':'stock'},{'LOWER':'index'}],
    [{'LOWER':'nikkei'},{"ORTH": '225','OP':'?'},{'LOWER':'index','OP':'?'}],
    [{'LOWER':'nikkei'},{'LOWER':'stock'},{'LOWER':'average'}],
    [{'LOWER':'hsi'},],
    [{'LOWER':'hang'},{'LOWER':'seng'},{'LOWER':'index'}],
    [{'LOWER':'hang'},{'LOWER':'seng'}],
    [{'LOWER':'ecb'}],
    [{'LOWER':'europian'},{'LOWER':'central'},{'LOWER':'bank'}],
    [{'LOWER':'boe'}],
    [{'LOWER':'boc'}],
    [{'LOWER':'boj'}],
    [{'LOWER':'bank'},{'LOWER':'of'},{'LOWER':'england'}],
    [{'LOWER':'bank'},{'LOWER':'of'},{'LOWER':'japan'}],
    [{'LOWER':'bank'},{'LOWER':'of'},{'LOWER':'canada'}],
    [{'LOWER':{'REGEX':'fed[eral]?'}},{'LOWER':'reserve'},{'LOWER':'bank'}],
    [{'LOWER':"russia's"},{'LOWER':'central'},{'LOWER':'bank'}]
    
])
matcher_2 = Matcher(nlp.vocab)
matcher_2.add('NASDAQ100',[
    [{'LOWER':'nasdaq100'}],
    [{'LOWER':'nasdaq'},{'ORTH':"100", 'OP':'?'}]
]) 
matcher_2.add('S&P500',[
    [{'LOWER':'s&p500'}],
    [{'LOWER':'sp500'}],
    [{"LOWER": "sp"}, {"ORTH": "500"}],
    [{"LOWER": "s&p"}, {"ORTH": "500"}]
])
matcher_2.add('DJIA',[
    [{'LOWER':'dow'},{'LOWER':'jones'}],
    [{'LOWER':'djia'}],
    [{'LOWER':'dow'},{'LOWER':'jones'},{'LOWER':'industrial'},{'LOWER':'average'}]
    
])
matcher_2.add('FTSE',[
    [{'LOWER':'ftse'},{"ORTH": '100','OP':'?'}],
    [{'LOWER':'financial'},{'LOWER':'times'},{'LOWER':'stock'},{'LOWER':'exchange'}],
    [{'LOWER':'footsie'}]
    
])
matcher_2.add('DAX',[
    [{'LOWER':'dax'}],
    [{'LOWER':'dax'},{"ORTH": '40','OP':'?'}],
    [{'LOWER':'german'},{'LOWER':'stock'},{'LOWER':'index'}]
    
])
matcher_2.add('N225',[
    [{'LOWER':'nikkei'},{"ORTH": '225','OP':'?'},{'LOWER':'index','OP':'?'}],
    [{'LOWER':'nikkei'},{'LOWER':'stock'},{'LOWER':'average'}]
    
])
matcher_2.add('HSI',[
    [{'LOWER':'hsi'},],
    [{'LOWER':'hang'},{'LOWER':'seng'},{'LOWER':'index','OP':'?'}]
    
])


In [5]:
special_cases = {}
def custom_tokenizer(nlp):
    return Tokenizer(nlp.vocab, rules=special_cases)


tokenizer = custom_tokenizer(nlp)

In [6]:
def match_tokens(text):
    if (text and type(text) == str):
        classes = []
        tokens = nlp(text)
        matches = matcher(tokens)
        for match_id, start, end in matches:
            string_id = nlp.vocab.strings[match_id]  # Get string representation
            classes.append(string_id)
            span = tokens[start:end]  # The matched span
        return set(classes)
    return set([])

In [8]:
articles['classes']= articles['summary'].map(lambda x: list(match_tokens(x)))

articles['classes_body']= articles['body'].map(lambda x: list(match_tokens(" ".join(x))))

articles['classes_title']= articles['title'].map(lambda x: list(match_tokens(x)))

In [9]:
no_summary = []
mismatch_sum_title = []
mismatch_sum_body = []
for idx,article in articles.iterrows():
   
    if len(article['classes_title'])== 0:
        print(article['title'])
    if len(article['classes'])== 0:
        no_summary.append(idx)
    if len(article['classes']) != len(article['classes_title']):
        mismatch_sum_title.append(idx)
    if len(article['classes']) != len(article['classes_body']):
        mismatch_sum_body.append(idx)

Taiwan punishes Deutsche Bank, others in currency speculation case
Surge in use of algorithms may hurt quality of FX prices - BIS
Vote and virus: volatile markets bring reminder of March turmoil
Analysis: Move over bonds, FX taking over as investors' new favourite playbook
Asian markets set to push higher after overnight gains
Currency markets in subdued mood ahead of key Fed speech
North America, UK daily forex volumes down in April - surveys
CEE FX to resist second wave fears, focus on economic recovery - Reuters poll
Emerging FX to firm a bit more, but recovery stymied by COVID-19 - Reuters poll
Bullish bets on most Asian currencies climb on vaccine hopes, China stability - Reuters poll
CEE currencies seen gaining in post-virus economic recovery - Reuters poll
Explainer: Hong Kong's currency finds strength in testing times
Commodity currencies down as OPEC+ deal fails to soothe demand concerns
Global currency funds notch wins amid coronavirus volatility
Emerging market turmoil may b

Boris Bounce? No So Fast, Brexit And Coronavirus Fears Make A Recovery Non-Essential
Coronavirus Chronicle: How The Pandemic Impacted The Forex Market
Three Scenarios For Trump’s Statement On Iran – And Potential Currency Reactions
Elliott Wave Analysis: Gold Looking Higher After A Fourth Wave
Fed Set To Provide Guidance For 2020 – Live
Natural Gas Ready To Rally Amid A Cold Snap
Non-Farm Payrolls Set For Sub-100K Levels – Live
To Cut Or Not To Cut? Powell’s Power-Play – Live
US GDP And ADP Live Coverage
The Last Draghi Show – Live
Parliament Votes On Boris Johnson’s Brexit – Live Coverage
Cryptocurrency Market Update: Major Cryptos Stay Quiet On Saturday
PBOC Hires Six Tech Experts For Its Upcoming Digital Currency
XMR, DASH, ZEC, ZEN And SBTC Delisted By OKEx Korea
Ripple Rebrands Products, Removes XRapid, XVia And XCurrent Mentions From Its Website
French Billionaire: Libra Is Unstoppable
Wall Street Rallies On US/China Trade Deal Phase 1 Agreement
Federal Reserve’s  Kaplan: Concern

Turn Around Tuesday Began On Monday
Friday's Nonfarm Payrolls Should Lower Expectations For Fed Policy Tightening
Treasury Yields Continue To Move Higher
Nonfarm Payrolls: Traders Eye March For Interest Rate Liftoff
Fed's Minutes Roils Markets
Fairly Average Week For Currencies
NFP Report To Kick Off New Year, Inject Life Into Muted FX Market
Currency Outlook: What To Expect From Key Pairs
Will The Bulls Dominate Stocks Or Do Bumpier Times Lie Ahead In 2022?
Volatility Could Continue For Loonie
Week Ahead – Markets wind down, mind the liquidity gap  
Will GDP Lift The Loonie?
Forex Traders Must Brace For Volatility In 2022  
Omicron Relief Kicks In, Riskier Trades Recover
Nerves Calm Down But Risks Still Loom
Santa Eluding Markets This Year
Assets That Could Outperform In Higher Rates, Inflation Environment
Gold Trapped Below $1,800; Bias Cautiously Bullish  
Events Will Traders Be Watching This Week
FX Strength And Weakness In 2021; The Problems Of COVID And Inflation Over Time
Centra

Currency markets are Sleepless in Seattle
US After the Close: Alphabet crushes, Apple and Microsoft strong beats but shares drift lower, little rally from API draw, Gold anchored at $1800
Currency markets consolidate
Asian equities edge lower
Currency markets content to range-trade
Will Canada’s job data lift loonie?
Canada GDP expected to decline
Currency markets looking for cues
Week Ahead – Doves are back in control
Currency markets remain cautious
US Close: Hawkish Bullard sinks stocks, Oil higher as US output to remain low, Gold stumbles after Bullard, Crypto sinks
New Zealand higher ahead of GDP
Market Insights Podcast (Episode 205)
US Open: Stocks edge higher, Focus on a less dovish Fed, Consumer inflation expectations decline
Currency markets remain in an induced coma
Currency markets remained rangebound
New Zealand slips, Business Confidence next
Canadian job data slips, NFP jumps
Oil claws higher, gold closes in on 1900
Markets eye US, Canadian job data
US Close – Stocks soft

RBA cuts rates on virus impact
Indices hit corrective mode
Gold – Retains its shine (video)
US Open – Virus fears intensifies, Johnson plays hardball, Oil’s demand shock, Gold rises
Asia Morning: South Korea Keeps Its Nerve
Risk pressure continues
A pause for breath?
Asia Morning: Another Tough Day At The Office
Asia’s Morning: Is All the Bad News Priced In?
Gold at 7-year high on virus fears
Coronavirus Concerns Crush V-Shaped Optimism
OANDA Market Insights – Episode 102 (Podcast)
Week ahead – Race to face the Don
Asia Finishes the Week with Sniffles
Gold breaks through $1,600 (video)
China Cuts Loan Prime Rates and Coronavirus Cases
Asia Session: Asia Discards The Apples
Gold firmer as death toll tops 2,000
And I Rand, I Rand So Far Away
Markets quiet on US holiday
Asia On Its Own On President’s Day
Week Ahead – Turning a Corner on COVID-19
Markets steady after yesterday’s shock
‘Is this a good deal, or should I run for the hills?’ My boyfriend of five years wants me to give him a $1

...

Why “Return By Easter” Is An Economic Pipe Dream
Markets Ending The Week On Better Note
DXY: Greenback’s Pullback May Be Short-Lived
Equities Jump On Hopes Of Restart
Markets: Trending Or Range-Bound?
Oil Firm, Greenback Extends Gains
Currency Market Still Pricing In Coronavirus Impact
Delta Air stock slips after wider-than-expected loss
Concerned That Asia Could Blow A Hole In Future Economic Recovery
Infinite Fed Easing, Finite Market Bounce
Is China In Recovery?
Nervousness Ahead Of The Weekend
Entry And Re-Entry On Cable Using Volume Price Analysis
Just When You Thought Initial Claims Couldn’t Be Any Worse
Dow ends up 550 points, stocks jolt higher after Fed’s Brainard calls for ‘sustained’ large-scale asset purchases
‘Sheer incompetence!’ Donald Trump Jr. shreds his father — or at least that’s how it appears in this viral clip
Wells Fargo blames COVID-19 and Fed rules, but also itself for disappointing results
Ricky Gervais talks ‘cancel culture’ and says even ‘mildly conservative

Trump administration has lost rationality – Global Times
Natural Gas Futures: Extra advances seem unlikely
Morgan stanley earning report: Could it be the catalyst to take the market higher?
Australian PM Morrison: July jobs data to be worse due to reimposed lockdown
UK’s Sharma: Jobs data would have been worse without govt support
Victoria records highest-ever daily total with 317 new cases
China's Pres. Xi: Long-term sound economic growth have not changed and will not change
OPEC+ to ease output cuts from August
WTI Price Analysis: Rising wedge on hourly chart keep sellers hopeful above $41.00
New South Wales Health Dpt: 10 new Covid-19 cases in 24 hour period
When is China’s Q2 GDP and how could it affect the market sentiment?
US is said to be weighing travel ban on Chinese Communist Party members – NYT
China to be more resolute in countering US, intolerant to city opposition – Global Times
NZ CPI arrives as expected, 1.5% YoY
WTI bears attack $41.00 in Asia as risk dwindles
White Ho

Tesla’s prayer for profit, earnings tests for Intel and Microsoft highlight first big week of coronavirus-tainted earnings
Mid-Afternoon Market Update: Nasdaq rises 40 points; NIO shares plummet
Gold: Next week's key macroeconomic events to keep an eye on
Greek PM Mitsotakis: Not enough progress to reach agreement
Forex Today: EU leaders can’t reach an agreement on the EU rescue fund
Weekly Column: Here we go again
Cycle Trading: Weekend report preview
Synchronization of the business cycle
Week Ahead: Focus remains on virus spread, fiscal stimulus, rebounding data, and earnings
Wall Street Next Week: Financial astrology for the successful investor & trade
Defiant Fauci tells InStyle magazine: ‘With all due modesty, I think I’m pretty effective’
Ranges may fray, but do you play for the breakout?
Is the ‘great rotation’ in the stock market under way as coronavirus cases surge? Or is it a false dawn? Here’s what experts think
EU's Michel offers revised plan for recovery fund – Reuters
We 

‘Something had really been missing from my life.’ Why I ditched San Francisco for Savannah, where the median home costs just $285,000
‘Please help!’ It seems like I have been paying my child’s student loan forever. How much longer must I pay it off?
These tax traps could derail your early retirement plan
White House says it will extend student-loan pause again before Aug. 31 or finalize plan by then on canceling student debt
Stocks tanked in the first quarter, and new research shows there should be a reversal by the end of June
Why more workers and companies are switching to freelance gigs
I no longer drive and want to retire in a highly walkable urban area with many cultural activities — where should I go?
Asian markets fall, trading muted with Good Friday holidays
Asian markets track Wall Street higher as oil prices retreat
Asian markets mostly rise on interest rate, inflation hopes
Fed’s Brainard welcomes signs of moderation in March ‘core’ consumer inflation
New York manufacturing 

Marketmind: 1%, 2%, 3%..
Raiffeisen Bank eyes options including exit for Russian unit
Stocks rise, U.S. yields slip as markets await Fed rate hike
Australia’s central bank hikes interest rates, flags more to come
Marketmind: Humble pie on central bankers’ menu
Cryptoverse: Venture capitalists catch crypto fever
EU prepares next Russia sanctions including German-backed oil ban
U.S. stocks gain in seesaw session, benchmark Treasury yield hits 3% ahead of Fed
Czech central bank seen raising main rate to 5.50%, highest since 1999: Reuters poll
Take Five: A central bank bonanza
Swiss industry and households feel strain from rising prices-data
Marketmind: Peak hawkishness
Russia swerves to avoid default: what is next?
Japan’s low-cost soul food noodles may become casualty of Ukraine war
Ukraine central bank makes changes to foreign currency market to protect reserves
Russia lowers key rate sharply to 14%, eyes more cuts
Bloomberg reporters in Turkey acquitted over 2018 currency crisis articl

In [11]:
articles['target'] = articles['classes_title'] + articles['classes'] + articles['classes_body']
articles['target'] =articles['target'].map(lambda x: list(set(x)))

In [12]:
empty = articles[articles['target'].str.len() == 0]

In [13]:
empty= pd.DataFrame(empty)

In [14]:
empty.reset_index(drop=True)

_id  \
0     623d63c46e887c1f5ed1a5ef   
1     623d64746e887c1f5ed1a6f7   
2     624432830524426478c683d9   
3     624432910524426478c68407   
4     624432910524426478c6840f   
...                        ...   
2638  62854f1353367d2c703d4870   
2639  62854f5053367d2c703d48ce   
2640  62854f7853367d2c703d4904   
2641  62854fd0f9be0f7f59082a33   
2642  62854feb42a7e414e15f069e   

                                                  title  \
0     Foreign exchange turnover drops for a second c...   
1     Forex daily trading volumes rise to $1.75 tril...   
2       What Trading Style Best Suits Your Personality?   
3                         A Guide to Trading Psychology   
4            3 Key Tips to Becoming A Successful Trader   
...                                                 ...   
2638  Data Avalanche To Keep Spotlight On Rate Hike ...   
2639  Fed To Speed Up Rate Hikes. How Far Will Powel...   
2640                                  Gold Consolidates   
2641              Market Insights Podcast (Episode 324)   
2642  Senate gives Fed Chairman Powell vote of confi...   

                                                summary  \
0     Average daily foreign exchange trading volumes...   
1     Average daily foreign exchange trading volumes...   
2     Trading style often aligns with personality an...   
3     The psychology of trading is often overlooked ...   
4     Whether you are an experienced or first-time t...   
...                                                 ...   
2638  It’s going to be a full-on week for economic i...   
2639  The Fed is almost certain to raise interest ra...   
2640  Looking at gold's chart, we can see it was tra...   
2641  Jonny Hart looks back on the week's business a...   
2642                                                NaN   

                                                   body classes classes_body  \
0     [By Reuters Staff, 2 MIN READ, LONDON (Reuters...      []           []   
1     [By Reuters Staff, 1 MIN READ, LONDON (Reuters...      []           []   
2     [- Reviewed by James Stanley, Nov. 24, 2021, T...      []           []   
3     [The psychology of trading is often overlooked...      []           []   
4     [Ask an experienced trader about mistakes she’...      []           []   
...                                                 ...     ...          ...   
2638  [The week will kick off with the monthly dump ...      []           []   
2639  [Fed officials have been talking a big game la...      []           []   
2640  [Looking at gold's chart, we can see it was tr...      []           []   
2641  [Jonny Hart looks back on the week’s business ...      []           []   
2642  [Federal Reserve Chairman Jerome Powell on Thu...      []           []   

     classes_title target  
0               []     []  
1               []     []  
2               []     []  
3               []     []  
4               []     []  
...            ...    ...  
2638            []     []  
2639            []     []  
2640            []     []  
2641            []     []  
2642            []     []  

[2643 rows x 8 columns]

In [15]:
index = 18

for x,i in empty.iterrows():
    print(i['summary'])

Average daily foreign exchange trading volumes fell 4.2% year-on-year in November, CLS said on Monday, as long-running trade talks between the United States and China and the run-up to the British election suppressed broader market volatility.
Average daily foreign exchange trading volumes rose 6.7% year-on-year in July to $1.75 trillion (£1.44 trillion), CLS said on Thursday, as a pick-up in volatility encouraged more buying and selling of currencies.
Trading style often aligns with personality and lifestyle and influences a trading strategy and plan.
The psychology of trading is often overlooked but is a key part of a professional trader’s skillset.
Whether you are an experienced or first-time trader, there are certain patterns to follow that can separate you from being a profitable trader or one that loses money.
The Fed and government’s support has altered how Americans think of saving versus investing. This is acting to kindle ‘animal spirits,’ in every sense of the Keynesian fash

nan
nan
nan
nan
nan
nan
As 2021 wound to a close, the animal spirits that had become the stock market for much of the previous year were being broken. Then in Q1 the market itself broke. The recent decline was deep, but h...
Supply chain issues plagued the semiconductor space starting in 2020 and continuing into this year. The semiconductor stocks however seemed unphased as the VanEck Semiconductor ETF (SMH) rallied to...
The price of oil spiked to a fresh yearly high ($130.50) in March amid the disruptions caused by the Russia-Ukraine war. Current market conditions may lead to higher crude prices as expectations fo...
Whether we blame rising rates, supply chain issues, or the war in Ukraine, the semiconductor space has seen significant downside this year with SMH down 16% to end the first quarter of trading.
LONDON (Reuters) – Russia said on Sunday that peace talks had not progressed enough for a leaders’ meeting and that Moscow’s position on the status of Crimea and Donbas remained u

nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Investors in Cinemark Holdings, Inc.  (NYSE:CNK)  need to pay close attention to the stock based on moves in the options market lately. That is because the Apr 17, 2020 $20.00 Put had some of the...
Investors in Dave & Buster’s Entertainment, Inc.  (NASDAQ:PLAY)  need to pay close attention to the stock based on moves in the options market lately. That is because the Apr 17, 2020 $5.00...
nan
Greif, Inc.  (NYSE:GEF)  was a big mover last session, as the company saw its shares rise more than 8% on the day. The move came on solid volume too with far more shares changing hands than in a...
nan
Pre-Open market analysisThe Emini finally 

nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Wall Street was set to open lower for the second straight session on Tuesday, after a report that th...
Oil steadied on Wednesday ahead of the Energy Information Administration (EIA) report, following sev...
The weak producer inflation readings reported by the Labor Department on Tuesday came against the ba...
U.S. producer prices unexpectedly fell in September, leading to the smallest annual increase in near...
Oil prices fell on Tuesday as Washington’s blacklisting of more Chinese companies dampened hopes f...
nan
nan
Ireland’s finance minister warned that the country’s government remains “highly skeptical” a...
Gold futures headed lower Friday, putting bullion on track to record its steepest weekly drop in mor...
President Donald Trump and Federal Reserve Chairman Jerome Powell, who have been at odds over the di...
U.S. import prices rose modestly in Septem

In [25]:
articles.applymap(lambda x: print(x))

623d62126e887c1f5ed1a34e
623d62126e887c1f5ed1a350
623d62126e887c1f5ed1a34c
623d62126e887c1f5ed1a351
623d62126e887c1f5ed1a352
623d62126e887c1f5ed1a353
623d62126e887c1f5ed1a354
623d621a6e887c1f5ed1a356
623d621a6e887c1f5ed1a357
623d62126e887c1f5ed1a355
623d621a6e887c1f5ed1a358
623d621a6e887c1f5ed1a359
623d621a6e887c1f5ed1a35a
623d621a6e887c1f5ed1a35b
623d621a6e887c1f5ed1a35c
623d621a6e887c1f5ed1a35d
623d621a6e887c1f5ed1a35e
623d621a6e887c1f5ed1a35f
623d62206e887c1f5ed1a360
623d62206e887c1f5ed1a361
623d62206e887c1f5ed1a362
623d62206e887c1f5ed1a364
623d62206e887c1f5ed1a363
623d62206e887c1f5ed1a366
623d62206e887c1f5ed1a365
623d62206e887c1f5ed1a368
623d62206e887c1f5ed1a367
623d62206e887c1f5ed1a369
623d62266e887c1f5ed1a36a
623d62266e887c1f5ed1a36b
623d62266e887c1f5ed1a36c
623d62266e887c1f5ed1a36d
623d62266e887c1f5ed1a36f
623d62266e887c1f5ed1a36e
623d62266e887c1f5ed1a370
623d62266e887c1f5ed1a371
623d62266e887c1f5ed1a372
623d622b6e887c1f5ed1a374
623d62266e887c1f5ed1a373
623d622b6e887c1f5ed1a375


624433860524426478c686ab
624433860524426478c686ac
624433860524426478c686ad
624433860524426478c686ae
624433860524426478c686af
624433860524426478c686b0
624433860524426478c686b1
624433860524426478c686b2
624433860524426478c686b3
624433860524426478c686b4
624433860524426478c686b5
624433860524426478c686b6
624433860524426478c686b7
624433860524426478c686b8
624433860524426478c686b9
624433860524426478c686ba
624433860524426478c686bb
6244338d0524426478c686bc
6244338d0524426478c686bd
6244338d0524426478c686be
6244338d0524426478c686bf
6244338d0524426478c686c0
6244338d0524426478c686c1
6244338d0524426478c686c2
6244338d0524426478c686c3
6244338d0524426478c686c4
6244338d0524426478c686c5
6244338d0524426478c686c6
6244338d0524426478c686c7
6244338d0524426478c686c8
6244338d0524426478c686c9
6244338d0524426478c686ca
6244338d0524426478c686cb
6244338d0524426478c686cc
6244338d0524426478c686cd
6244338d0524426478c686ce
6244338d0524426478c686cf
624433940524426478c686d0
624433940524426478c686d1
624433940524426478c686d2


624437927c7dfe1ae873ba4d
624437927c7dfe1ae873ba4e
624437927c7dfe1ae873ba4f
624437927c7dfe1ae873ba50
624437927c7dfe1ae873ba51
624437927c7dfe1ae873ba52
6244379c7c7dfe1ae873ba53
6244379c7c7dfe1ae873ba54
6244379c7c7dfe1ae873ba55
6244379c7c7dfe1ae873ba56
6244379c7c7dfe1ae873ba57
6244379c7c7dfe1ae873ba58
6244379c7c7dfe1ae873ba59
6244379c7c7dfe1ae873ba5a
6244379c7c7dfe1ae873ba5b
6244379c7c7dfe1ae873ba5c
6244379c7c7dfe1ae873ba5d
624437a67c7dfe1ae873ba5e
624437a67c7dfe1ae873ba5f
624437a67c7dfe1ae873ba60
624437a67c7dfe1ae873ba61
624437a67c7dfe1ae873ba62
624437a67c7dfe1ae873ba63
624437a67c7dfe1ae873ba64
624437a67c7dfe1ae873ba65
624437a67c7dfe1ae873ba66
624437a67c7dfe1ae873ba67
624437a67c7dfe1ae873ba68
624437b07c7dfe1ae873ba69
624437b07c7dfe1ae873ba6a
624437b07c7dfe1ae873ba6b
624437b07c7dfe1ae873ba6c
624437b07c7dfe1ae873ba6d
624437b07c7dfe1ae873ba6e
624437b07c7dfe1ae873ba6f
624437b07c7dfe1ae873ba70
624437b07c7dfe1ae873ba71
624437b07c7dfe1ae873ba72
624437b07c7dfe1ae873ba73
624437bb7c7dfe1ae873ba74


62443f944bbbb4df3b9214b5
62443f944bbbb4df3b9214b6
62443f944bbbb4df3b9214b7
62443f944bbbb4df3b9214b8
62443f944bbbb4df3b9214b9
62443f944bbbb4df3b9214ba
62443f944bbbb4df3b9214bb
62443f944bbbb4df3b9214bc
62443f944bbbb4df3b9214bd
62443f944bbbb4df3b9214be
62443f9e4bbbb4df3b9214bf
62443f9e4bbbb4df3b9214c0
62443f9e4bbbb4df3b9214c1
62443f9e4bbbb4df3b9214c2
62443f9e4bbbb4df3b9214c3
62443f9e4bbbb4df3b9214c4
62443f9e4bbbb4df3b9214c5
62443f9e4bbbb4df3b9214c6
62443f9e4bbbb4df3b9214c7
62443f9e4bbbb4df3b9214c8
62443f9e4bbbb4df3b9214c9
62443f9e4bbbb4df3b9214ca
62443f9e4bbbb4df3b9214cb
62443f9e4bbbb4df3b9214cc
62443f9e4bbbb4df3b9214cd
62443fa84bbbb4df3b9214ce
62443fa84bbbb4df3b9214cf
62443fa84bbbb4df3b9214d0
62443fa84bbbb4df3b9214d1
62443fa84bbbb4df3b9214d2
62443fa84bbbb4df3b9214d3
62443fa84bbbb4df3b9214d4
62443fa84bbbb4df3b9214d5
62443fa84bbbb4df3b9214d6
62443fa84bbbb4df3b9214d7
62443fa84bbbb4df3b9214d8
62443fa84bbbb4df3b9214d9
62443fa84bbbb4df3b9214da
62443fa84bbbb4df3b9214db
62443fa84bbbb4df3b9214dc


624445efde4f8e740ef178f1
624445efde4f8e740ef178f2
624445efde4f8e740ef178f3
624445efde4f8e740ef178f4
624445efde4f8e740ef178f5
624445efde4f8e740ef178f6
624445efde4f8e740ef178f7
624445efde4f8e740ef178f8
624445efde4f8e740ef178f9
624445efde4f8e740ef178fa
624445efde4f8e740ef178fb
624445efde4f8e740ef178fc
624445efde4f8e740ef178fd
624445efde4f8e740ef178fe
624445efde4f8e740ef178ff
624445efde4f8e740ef17900
624445efde4f8e740ef17901
624445efde4f8e740ef17902
624445efde4f8e740ef17903
624445efde4f8e740ef17904
624445f6de4f8e740ef17905
624445f6de4f8e740ef17906
624445f6de4f8e740ef17907
624445f6de4f8e740ef17908
624445f6de4f8e740ef17909
624445f6de4f8e740ef1790a
624445f6de4f8e740ef1790b
624445f6de4f8e740ef1790c
624445f6de4f8e740ef1790d
624445f6de4f8e740ef1790e
624445f6de4f8e740ef1790f
624445f6de4f8e740ef17910
624445f6de4f8e740ef17911
624445f6de4f8e740ef17912
624445f6de4f8e740ef17913
624445f6de4f8e740ef17914
624445f6de4f8e740ef17915
624445f6de4f8e740ef17916
624445f6de4f8e740ef17917
624445f6de4f8e740ef17918


...

['USD', 'EUR']
['INDEX']
['INDEX']
['INDEX']
['EUR']
['EUR']
['JPY', 'USD']
['USD', 'EUR']
['JPY', 'EUR', 'AUD', 'CAD', 'USD', 'INDEX']
['GBP', 'USD', 'EUR']
[]
['OIL']
['GBP', 'INDEX', 'EUR']
['GBP', 'INDEX', 'USD', 'EUR']
['CAD', 'USD']
['USD', 'EUR']
[]
['JPY', 'USD']
['EUR']
['GBP', 'JPY']
['INDEX', 'EUR']
['GBP', 'OIL', 'JPY', 'NZD', 'EUR', 'AUD', 'CAD', 'USD', 'INDEX']
['INDEX', 'XAU']
['EUR']
['INDEX', 'USD']
['USD']
['USD']
[]
['JPY', 'USD', 'EUR']
['JPY', 'USD', 'EUR']
['USD', 'EUR']
['USD']
['GBP', 'JPY', 'NZD', 'EUR', 'USD', 'RUB']
['JPY', 'EUR', 'AUD', 'USD', 'INDEX']
[]
['OIL', 'JPY', 'EUR', 'AUD', 'CAD', 'USD', 'INDEX']
['GBP', 'EUR']
['USD', 'EUR']
['OIL']
['OIL', 'BTC', 'EUR', 'USD', 'INDEX']
['OIL', 'CAD', 'USD', 'EUR']
['GBP', 'JPY', 'EUR', 'AUD', 'MXN', 'USD', 'INDEX']
['USD', 'EUR']
['GBP', 'USD', 'EUR']
[]
['CAD', 'USD']
['USD']
['JPY', 'USD']
['INDEX']
['INDEX']
['JPY', 'USD']
['INDEX', 'EUR', 'XAU', 'USD']
['INDEX']
[]
['AUD', 'INDEX', 'USD']
['USD']
['CAD', 'USD

['INDEX']
['USD', 'EUR']
[]
['XAU']
['INDEX', 'USD', 'EUR']
['INDEX', 'USD']
['GBP', 'USD']
[]
['INDEX']
['MXN', 'USD']
['GBP', 'JPY', 'EUR', 'AUD', 'USD']
[]
[]
[]
['INDEX']
['INDEX']
[]
['GBP', 'INDEX', 'USD', 'EUR']
['GBP', 'JPY', 'NZD', 'AUD', 'USD', 'INDEX']
['GBP', 'OIL', 'JPY', 'EUR', 'AUD', 'USD', 'INDEX']
['INDEX', 'JPY', 'USD']
['OIL', 'INDEX']
['INDEX']
['USD']
['CAD', 'USD']
['GBP', 'USD', 'EUR']
['USD']
['OIL', 'INDEX', 'XAU', 'USD']
['INDEX']
['INDEX']
['INDEX']
['INDEX', 'USD']
['EUR']
[]
['INDEX', 'USD', 'EUR']
['JPY', 'OIL', 'CAD', 'USD']
[]
['INDEX']
['GBP', 'USD', 'BTC']
['INDEX', 'USD', 'EUR']
['INDEX']
['NZD', 'USD']
['INDEX']
['INDEX']
[]
['AUD', 'INDEX', 'JPY', 'USD']
['INDEX']
['GBP', 'JPY', 'NZD', 'EUR', 'AUD', 'USD', 'INDEX']
['INDEX', 'USD']
['GBP', 'INDEX', 'USD', 'EUR']
['OIL', 'JPY', 'NZD', 'XAU', 'AUD', 'USD', 'INDEX']
['OIL', 'JPY', 'NZD', 'AUD', 'USD', 'INDEX']
['OIL', 'NZD', 'XAU', 'AUD', 'CAD', 'USD', 'INDEX']
['INDEX']
['AUD', 'INDEX', 'JPY', 'USD']


['GBP', 'TRY', 'USD']
['INDEX']
['AUD', 'INDEX', 'USD', 'EUR']
[]
['USD']
[]
['INDEX', 'CAD', 'USD']
['USD', 'EUR']
['USD']
['USD', 'EUR']
['AUD', 'INDEX', 'JPY', 'USD']
[]
['NZD', 'USD']
['USD', 'EUR']
[]
['INDEX', 'USD', 'EUR']
['INDEX', 'JPY', 'USD']
['GBP', 'USD']
['USD', 'EUR']
['INDEX', 'EUR']
['TRY', 'INDEX']
[]
['INDEX', 'EUR']
['GBP', 'CHF', 'OIL', 'JPY', 'NZD', 'EUR', 'AUD', 'CAD', 'USD']
['CHF', 'CAD']
['GBP', 'EUR']
['OIL', 'JPY', 'NZD', 'EUR', 'AUD', 'INDEX', 'CNY']
['INDEX', 'JPY', 'USD']
[]
['INDEX']
[]
['JPY', 'USD']
['XAU', 'USD']
[]
['GBP', 'TRY', 'INDEX', 'EUR']
['INDEX', 'JPY', 'USD']
['GBP', 'NZD', 'EUR', 'AUD', 'CAD', 'USD', 'INDEX']
[]
['GBP', 'CHF', 'OIL', 'JPY', 'NZD', 'EUR', 'AUD', 'USD', 'INDEX']
['AUD', 'USD']
[]
['INDEX', 'EUR']
['GBP', 'CHF', 'JPY', 'NZD', 'TRY', 'EUR', 'USD', 'RUB']
['INDEX']
[]
['INDEX', 'JPY', 'USD']
['AUD', 'USD']
['XAU']
[]
[]
['TRY', 'INDEX', 'EUR']
['INDEX', 'EUR']
['GBP', 'JPY', 'EUR', 'USD', 'INDEX']
['XAU', 'USD']
['GBP', 'JPY', 

['INDEX', 'USD', 'EUR']
[]
['INDEX', 'EUR']
[]
['INDEX']
['EUR']
[]
['INDEX']
['GBP', 'EUR']
['INDEX', 'USD', 'EUR']
['GBP', 'EUR']
['GBP', 'JPY', 'EUR', 'USD', 'INDEX']
[]
['GBP']
['INDEX', 'EUR']
['GBP', 'EUR']
['USD', 'EUR']
['INDEX', 'JPY', 'EUR']
['INDEX', 'CNY']
[]
['TRY', 'EUR']
['GBP', 'CHF', 'JPY', 'EUR', 'USD', 'INDEX']
[]
[]
[]
[]
[]
['INDEX', 'JPY']
['GBP', 'NZD', 'EUR', 'AUD', 'USD', 'INDEX']
[]
['EUR']
[]
['INDEX', 'USD', 'CNY']
['INDEX']
[]
['TRY', 'INDEX', 'USD']
['EUR']
['EUR']
['INDEX']
['NZD', 'TRY', 'AUD', 'USD', 'INDEX']
[]
[]
['USD', 'CNY']
['GBP', 'CHF', 'JPY', 'EUR', 'USD', 'CNY']
[]
['INDEX']
[]
['INDEX']
['INDEX']
['OIL']
['INDEX', 'XAU', 'USD']
['GBP', 'OIL', 'JPY', 'EUR', 'AUD', 'USD', 'INDEX']
['AUD', 'USD']
['USD']
['USD', 'CNY']
['BTC']
['GBP', 'INDEX', 'EUR']
['AUD', 'USD']
['OIL']
['GBP', 'USD', 'EUR']
['GBP', 'JPY', 'EUR', 'AUD', 'USD', 'INDEX']
['GBP', 'JPY', 'EUR', 'AUD', 'USD', 'INDEX']
['INDEX', 'USD']
['INDEX', 'USD', 'EUR']
['GBP', 'USD']
[]
['IN

_id title summary  body classes classes_body classes_title target
0      None  None    None  None    None         None          None   None
1      None  None    None  None    None         None          None   None
2      None  None    None  None    None         None          None   None
3      None  None    None  None    None         None          None   None
4      None  None    None  None    None         None          None   None
...     ...   ...     ...   ...     ...          ...           ...    ...
27270  None  None    None  None    None         None          None   None
27271  None  None    None  None    None         None          None   None
27272  None  None    None  None    None         None          None   None
27273  None  None    None  None    None         None          None   None
27274  None  None    None  None    None         None          None   None

[27275 rows x 8 columns]

In [26]:
articles.head()

_id  \
0  623d62126e887c1f5ed1a34e   
1  623d62126e887c1f5ed1a350   
2  623d62126e887c1f5ed1a34c   
3  623d62126e887c1f5ed1a351   
4  623d62126e887c1f5ed1a352   

                                               title  \
0  Risk currencies recover from Friday carnage, d...   
1  Taiwan punishes Deutsche Bank, others in curre...   
2  BoE hikes, Fed pivots, ECB rolls slow as pande...   
3         Dollar extends rebound as U.S. yields rise   
4  Dollar recovery pushes sterling below $1.35; U...   

                                             summary  \
0  The Australian dollar and other riskier curren...   
1  Taiwan's central bank said on Sunday it had ba...   
2  (Reuters) -Britain became the first G7 economy...   
3  The dollar edged higher across the board on Mo...   
4  The pound was among the risk assets hurt by th...   

                                                body            classes  \
0  [By Reuters Staff, 3 MIN READ, TOKYO (Reuters)...         [AUD, USD]   
1  [By Reuters Staff, 3 MIN READ, TAIPEI (Reuters...         [TWD, USD]   
2  [Federal Reserve in Washington, U.S., November...              [EUR]   
3  [By Saqib Iqbal Ahmed, 3 MIN READ, NEW YORK (R...              [USD]   
4  [By Elizabeth Howcroft, 3 MIN READ, LONDON (Re...  [GBP, INDEX, USD]   

                            classes_body classes_title  \
0  [GBP, JPY, NZD, EUR, AUD, USD, INDEX]         [USD]   
1                             [TWD, USD]            []   
2                           [INDEX, EUR]       [INDEX]   
3                        [GBP, USD, BTC]         [USD]   
4                 [GBP, INDEX, USD, EUR]    [GBP, USD]   

                                  target  
0  [GBP, JPY, NZD, EUR, AUD, USD, INDEX]  
1                             [TWD, USD]  
2                           [INDEX, EUR]  
3                        [GBP, USD, BTC]  
4                 [GBP, INDEX, USD, EUR]

In [31]:
for i,x in articles.iterrows():
    db.contents.update_one({'_id':x['_id']},{'$set':{'classes_summary':x['classes'],'classes_body':x['classes_body'],'classes_target':x['target'],'classes_title':x['classes_title']}})